In [1]:
%pip install pybboxes

Note: you may need to restart the kernel to use updated packages.


In [2]:
import os
import re
import json
import shutil
from pybboxes import BoundingBox

In [3]:
val_dataset_path = 'FLIR_A2/images_thermal_val/data'
val_images = sorted(os.listdir(val_dataset_path))
val_images_paths = [os.path.join(val_dataset_path, image) for image in val_images]

train_dataset_path = 'FLIR_ADAS_v2/images_thermal_train/data'
train_images = sorted(os.listdir(train_dataset_path))
train_images_paths = [os.path.join(train_dataset_path, image) for image in train_images]

test_dataset_path = 'FLIR_ADAS_v2/video_thermal_test/data'
test_images = sorted(os.listdir(test_dataset_path))
test_images_paths = [os.path.join(test_dataset_path, image) for image in test_images]

with open('FLIR_ADAS_v2/images_thermal_val/index.json', 'r') as file:
    val_annotations_data = json.load(file)
val_frames_annotations = val_annotations_data['frames']

with open('FLIR_ADAS_v2/images_thermal_train/index.json', 'r') as file:
    train_annotations_data = json.load(file)
train_frames_annotations = train_annotations_data['frames']

with open('FLIR_ADAS_v2/video_thermal_test/index.json', 'r') as file:
    test_annotations_data = json.load(file)
test_frames_annotations = test_annotations_data['frames']

dataset_classes = {
  0: "animal",
  1: "bike",
  2: "bird",
  3: "bus",
  4: "car",
  5: "dog",
  6: "face",
  7: "hydrant",
  8: "license plate",
  9: "light",
  10: "motor",
  11: "other vehicle",
  12: "person",
  13: "rider",
  14: "scooter",
  15: "sign",
  16: "skateboard",
  17: "stroller",
  18: "train",
  19: "truck",
}

FileNotFoundError: [Errno 2] No such file or directory: 'FLIR_ADAS_v2/images_thermal_val/data'

In [ ]:
def getFrameId(image_path):
  pattern = r'frame-(\w+)-(\w+).jpg'
  matchedPattern = re.search(pattern, image_path)

  if matchedPattern:
    return matchedPattern.group(2)
  else:
    return None
      
def getFrameAnnotations(frameId, dataset):
  if dataset == 'train':
    frame = next((frame for frame in train_frames_annotations if frame['datasetFrameId'] == frameId), None)
  elif dataset == 'val':
    frame = next((frame for frame in val_frames_annotations if frame['datasetFrameId'] == frameId), None)
  elif dataset == 'test':
    frame = next((frame for frame in test_frames_annotations if frame['datasetFrameId'] == frameId), None)

  if frame:
    return frame['annotations']
  else:
    return None

def getFrameSize(frameId, dataset):  
  if dataset == 'train':
    frame = next((frame for frame in train_frames_annotations if frame['datasetFrameId'] == frameId), None)
  elif dataset == 'val':
    frame = next((frame for frame in val_frames_annotations if frame['datasetFrameId'] == frameId), None)
  elif dataset == 'test':
    frame = next((frame for frame in test_frames_annotations if frame['datasetFrameId'] == frameId), None)
  
  if frame:
    return frame['width'], frame['height']
  else:
    return None

def getIdByLabel(label):
  for category_id, category_label in dataset_classes.items():
    if category_label == label:
      return category_id
  return None

In [ ]:
train_unique_labels = []
for image_path in train_images_paths:
  frameId = getFrameId(image_path)
  annotations = getFrameAnnotations(frameId, 'train')
  for annotation in annotations:
    if annotation['labels'][0] not in train_unique_labels:
      train_unique_labels.append(annotation['labels'][0])

train_unique_labels.sort()
print("Classes in train dataset: ", train_unique_labels)

val_unique_labels = []
for image_path in val_images_paths:
  frameId = getFrameId(image_path)
  annotations = getFrameAnnotations(frameId, 'val')
  for annotation in annotations:
    if annotation['labels'][0] not in val_unique_labels:
      val_unique_labels.append(annotation['labels'][0])

val_unique_labels.sort()
print("Classes in val dataset: ", val_unique_labels)

test_unique_labels = []
for image_path in test_images_paths:
  frameId = getFrameId(image_path)
  annotations = getFrameAnnotations(frameId, 'test')
  for annotation in annotations:
    if annotation['labels'][0] not in test_unique_labels:
      test_unique_labels.append(annotation['labels'][0])

test_unique_labels.sort()
print("Classes in test dataset: ", test_unique_labels)

In [93]:
def generateImagesAndLabels(images_paths, dataset):
  for image_path in images_paths:
    frameId = getFrameId(image_path)
    width, height = getFrameSize(frameId, dataset)
    annotations = getFrameAnnotations(frameId, dataset)
    
    new_image_path = 'data/images/'+dataset+'/'+frameId+'.jpg'
    shutil.copy(image_path, new_image_path)
  
    labels_path = 'data/labels/'+dataset+'/'+frameId+'.txt'
    with open(labels_path, 'w') as f:
      for annotation in annotations:
        labelId = getIdByLabel( annotation['labels'][0])
        bbox = [int(annotation['boundingBox']['x']), int(annotation['boundingBox']['y']), int(annotation['boundingBox']['w']), int(annotation['boundingBox']['h'])]
        coco_bbox = BoundingBox.from_coco(*bbox, image_size=(width, height))
        x,y,w,h = coco_bbox.to_yolo(return_values=True)
        line = f"{labelId} {x} {y} {w} {h}\n"
        f.write(line)

In [94]:
#generateImagesAndLabels(test_images_paths, 'test')

L6K5SC6fYjHNC8uff test
{'annotations': [{'boundingBox': {'h': 21, 'w': 47, 'x': 263, 'y': 217}, 'labels': ['car'], 'source': {'meta': {'tool': 'conservator', 'user': 'SWmSAtrcP4MAWMmxd'}, 'type': 'human'}, 'targetId': 0}, {'boundingBox': {'h': 49, 'w': 17, 'x': 86, 'y': 227}, 'labels': ['person'], 'source': {'meta': {'tool': 'conservator', 'user': 'SWmSAtrcP4MAWMmxd'}, 'type': 'human'}, 'targetId': 1}], 'datasetFrameId': 'L6K5SC6fYjHNC8uff', 'height': 512, 'isEmpty': False, 'isFlagged': False, 'md5': '089b2fe98d13773131d030dd5899235c', 'tags': [], 'videoMetadata': {'frameId': 'mk2R34oJFv75TnqcL', 'frameIndex': 745, 'videoId': '4FRnNpmSmwktFJKjg'}, 'width': 640}
9CgazXqHXeEATqtKz test
{'annotations': [{'boundingBox': {'h': 21, 'w': 47, 'x': 263, 'y': 217}, 'labels': ['car'], 'source': {'meta': {'tool': 'conservator', 'user': 'SWmSAtrcP4MAWMmxd'}, 'type': 'human'}, 'targetId': 0}, {'boundingBox': {'h': 48, 'w': 17, 'x': 86, 'y': 227}, 'labels': ['person'], 'source': {'meta': {'tool': 'co

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



YjEQ7fyfY9KMsz4qp test
{'annotations': [{'boundingBox': {'h': 86, 'w': 24, 'x': 478, 'y': 176}, 'labels': ['person'], 'source': {'meta': {'tool': 'conservator', 'user': 'X5XkSBsHmASqLiRcS'}, 'type': 'human'}, 'targetId': 13927}, {'boundingBox': {'h': 38, 'w': 50, 'x': 201, 'y': 188}, 'labels': ['car'], 'source': {'meta': {'tool': 'conservator', 'user': 'X5XkSBsHmASqLiRcS'}, 'type': 'human'}, 'targetId': 13937}, {'boundingBox': {'h': 26, 'w': 29, 'x': 237, 'y': 187}, 'labels': ['car'], 'source': {'meta': {'tool': 'conservator', 'user': 'X5XkSBsHmASqLiRcS'}, 'type': 'human'}, 'targetId': 13938}, {'boundingBox': {'h': 11, 'w': 9, 'x': 289, 'y': 184}, 'labels': ['car'], 'source': {'meta': {'tool': 'conservator', 'user': 'X5XkSBsHmASqLiRcS'}, 'type': 'human'}, 'targetId': 13939}, {'boundingBox': {'h': 26, 'w': 30, 'x': 292, 'y': 187}, 'labels': ['car'], 'source': {'meta': {'tool': 'conservator', 'user': 'X5XkSBsHmASqLiRcS'}, 'type': 'human'}, 'targetId': 13940}, {'boundingBox': {'h': 40, 'w

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



YJbkq5hZF3FDn9uDY test
{'annotations': [{'boundingBox': {'h': 29, 'w': 34, 'x': 288, 'y': 306}, 'labels': ['car'], 'source': {'meta': {'tool': 'conservator', 'user': 'JMAFXRpJMvSdRWySY'}, 'type': 'human'}, 'targetId': 49893}, {'boundingBox': {'h': 7, 'w': 7, 'x': 350, 'y': 314}, 'labels': ['car'], 'source': {'meta': {'tool': 'conservator', 'user': 'JMAFXRpJMvSdRWySY'}, 'type': 'human'}, 'targetId': 49899}, {'boundingBox': {'h': 78, 'w': 107, 'x': 454, 'y': 280}, 'labels': ['other vehicle'], 'source': {'meta': {'tool': 'conservator', 'user': 'JMAFXRpJMvSdRWySY'}, 'type': 'human'}, 'targetId': 49896}, {'boundingBox': {'h': 40, 'w': 35, 'x': 382, 'y': 294}, 'labels': ['other vehicle'], 'source': {'meta': {'tool': 'conservator', 'user': 'JMAFXRpJMvSdRWySY'}, 'type': 'human'}, 'targetId': 49894}, {'boundingBox': {'h': 36, 'w': 19, 'x': 415, 'y': 297}, 'labels': ['other vehicle'], 'source': {'meta': {'tool': 'conservator', 'user': 'JMAFXRpJMvSdRWySY'}, 'type': 'human'}, 'targetId': 49895}], 

In [62]:
#generateImagesAndLabels(train_images_paths, 'train')

In [64]:
#generateImagesAndLabels(val_images_paths, 'val')